# DuckDB and geoparquet

## Imports

In [1]:
import os
import duckdb
import folium
import pystac
import folium.plugins as folium_plugins
import geopandas as gpd
import pygeofilter
from stac_geoparquet.arrow import stac_table_to_items
from pygeofilter.backends.sql import to_sql_where
from pygeofilter.util import IdempotentDict
from collections import OrderedDict
from pygeofilter.parsers.cql2_json import parse as json_parse

In [2]:
# Install and load DuckDB spatial extension
duckdb.install_extension("spatial")
duckdb.load_extension("spatial")

In [3]:
s2_parquet_path = "s2-stac-api.parquet"

## Query the geoparquet file

In [4]:
if not os.path.exists(s2_parquet_path):
    print("Run notebook 02-Create a geoparquet file.ipynb first")
    exit(1)

In [7]:
sql_query = f"SELECT * EXCLUDE(geometry), ST_AsWKB(geometry) as geometry FROM '{s2_parquet_path}'"

print(sql_query)

db = duckdb.query(sql_query)

SELECT * EXCLUDE(geometry), ST_AsWKB(geometry) as geometry FROM 's2-stac-api.parquet'


In [8]:
type(db)

duckdb.duckdb.DuckDBPyRelation

## Convert DuckDB result to Arrow table

In [16]:
table = db.fetch_arrow_table()

#table_head = table.slice(0, 125)  # Get first 125 rows

In [10]:
# table.to_pandas()

In [11]:
table.slice(0, 4).to_pandas()

assets  \
0  {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
1  {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
2  {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
3  {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   

                                                bbox      collection  \
0  {'xmin': -10.25298175, 'ymin': 43.25815001, 'x...  sentinel-2-l2a   
1  {'xmin': 0.45686052, 'ymin': 44.13799675, 'xma...  sentinel-2-l2a   
2  {'xmin': 0.4959286, 'ymin': 43.2382626, 'xmax'...  sentinel-2-l2a   
3  {'xmin': 0.53321795, 'ymin': 42.33836183, 'xma...  sentinel-2-l2a   

                                                  id  \
0  S2B_MSIL2A_20231231T114409_R123_T29TMJ_2023123...   
1  S2A_MSIL2A_20231231T105441_R051_T31TCK_2023123...   
2  S2A_MSIL2A_20231231T105441_R051_T31TCJ_2023123...   
3  S2A_MSIL2A_20231231T105441_R051_T31TCH_2023123...   

                                               links  \
0  [{'href': 'https://planetarycomputer.microsoft...   
1  [{'href': 'https://planetarycomputer.microsoft...   
2  [{'href': 'https://planetarycomputer.microsoft...   
3  [{'href': 'https://planetarycomputer.microsoft...   

                                     stac_extensions stac_version     type  \
0  [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
1  [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
2  [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
3  [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   

  constellation                         datetime  ...  \
0    Sentinel 2 2023-12-31 11:44:09.024000+00:00  ...   
1    Sentinel 2 2023-12-31 10:54:41.024000+00:00  ...   
2    Sentinel 2 2023-12-31 10:54:41.024000+00:00  ...   
3    Sentinel 2 2023-12-31 10:54:41.024000+00:00  ...   

   s2:reflectance_conversion_factor s2:saturated_defective_pixel_percentage  \
0                          1.034040                                     0.0   
1                          1.034038                                     0.0   
2                          1.034038                                     0.0   
3                          1.034038                                     0.0   

  s2:snow_ice_percentage s2:thin_cirrus_percentage  \
0               0.000000                 40.464744   
1               0.129087                 13.664892   
2               0.000010                 18.065368   
3               0.055783                  4.123205   

   s2:unclassified_percentage  s2:vegetation_percentage s2:water_percentage  \
0                    0.000000                  0.000000            0.708269   
1                    0.000000                  0.000000            0.001739   
2                    0.000086                  0.000000            0.010481   
3                    0.047372                  0.522049            0.014681   

  sat:orbit_state sat:relative_orbit  \
0      descending                123   
1      descending                 51   
2      descending                 51   
3      descending                 51   

                                            geometry  
0  b'\x01\x03\x00\x00\x00\x01\x00\x00\x00\x0e\x00...  
1  b'\x01\x03\x00\x00\x00\x01\x00\x00\x00\x05\x00...  
2  b'\x01\x03\x00\x00\x00\x01\x00\x00\x00\x05\x00...  
3  b'\x01\x03\x00\x00\x00\x01\x00\x00\x00\x05\x00...  

[4 rows x 42 columns]

In [12]:
table_head = table.slice(0, 125)  # Get first 125 rows
# for item in stac_table_to_items(table_head):
#     print(item)

In [13]:
table_head.to_pandas()

assets  \
0    {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
1    {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
2    {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
3    {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
4    {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
..                                                 ...   
120  {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
121  {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
122  {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
123  {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   
124  {'AOT': {'gsd': 10.0, 'href': 'https://sentine...   

                                                  bbox      collection  \
0    {'xmin': -10.25298175, 'ymin': 43.25815001, 'x...  sentinel-2-l2a   
1    {'xmin': 0.45686052, 'ymin': 44.13799675, 'xma...  sentinel-2-l2a   
2    {'xmin': 0.4959286, 'ymin': 43.2382626, 'xmax'...  sentinel-2-l2a   
3    {'xmin': 0.53321795, 'ymin': 42.33836183, 'xma...  sentinel-2-l2a   
4    {'xmin': 0.5688037, 'ymin': 41.4388363, 'xmax'...  sentinel-2-l2a   
..                                                 ...             ...   
120  {'xmin': -4.67851734, 'ymin': 39.64771538, 'xm...  sentinel-2-l2a   
121  {'xmin': -1.84912778, 'ymin': 38.74919438, 'xm...  sentinel-2-l2a   
122  {'xmin': -1.8632824, 'ymin': 37.8524187, 'xmax...  sentinel-2-l2a   
123  {'xmin': -1.8681232, 'ymin': 37.5303524, 'xmax...  sentinel-2-l2a   
124  {'xmin': -3.00023345, 'ymin': 38.75403605, 'xm...  sentinel-2-l2a   

                                                    id  \
0    S2B_MSIL2A_20231231T114409_R123_T29TMJ_2023123...   
1    S2A_MSIL2A_20231231T105441_R051_T31TCK_2023123...   
2    S2A_MSIL2A_20231231T105441_R051_T31TCJ_2023123...   
3    S2A_MSIL2A_20231231T105441_R051_T31TCH_2023123...   
4    S2A_MSIL2A_20231231T105441_R051_T31TCG_2023123...   
..                                                 ...   
120  S2B_MSIL2A_20231229T110359_R094_T30TUK_2023122...   
121  S2B_MSIL2A_20231229T110359_R094_T30SXJ_2023122...   
122  S2B_MSIL2A_20231229T110359_R094_T30SXH_2023122...   
123  S2B_MSIL2A_20231229T110359_R094_T30SXG_2023122...   
124  S2B_MSIL2A_20231229T110359_R094_T30SWJ_2023122...   

                                                 links  \
0    [{'href': 'https://planetarycomputer.microsoft...   
1    [{'href': 'https://planetarycomputer.microsoft...   
2    [{'href': 'https://planetarycomputer.microsoft...   
3    [{'href': 'https://planetarycomputer.microsoft...   
4    [{'href': 'https://planetarycomputer.microsoft...   
..                                                 ...   
120  [{'href': 'https://planetarycomputer.microsoft...   
121  [{'href': 'https://planetarycomputer.microsoft...   
122  [{'href': 'https://planetarycomputer.microsoft...   
123  [{'href': 'https://planetarycomputer.microsoft...   
124  [{'href': 'https://planetarycomputer.microsoft...   

                                       stac_extensions stac_version     type  \
0    [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
1    [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
2    [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
3    [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
4    [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
..                                                 ...          ...      ...   
120  [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
121  [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
122  [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
123  [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   
124  [https://stac-extensions.github.io/eo/v1.1.0/s...        1.1.0  Feature   

    constellation                         datetime  ...  \
0      Sentinel 2 2023-12-31 11:44:09.024000+00:

## Map


In [17]:
all_items = [pystac.Item.from_dict(item) for item in stac_table_to_items(table)]
all_items

[<Item id=S2B_MSIL2A_20231231T114409_R123_T29TMJ_20231231T150806>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCK_20231231T162343>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCJ_20231231T162355>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCH_20231231T162350>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCG_20231231T162354>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCF_20231231T162151>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCE_20231231T162147>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TBG_20231231T162352>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TBF_20231231T162153>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TBE_20231231T162152>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31SCD_20231231T162143>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31SCC_20231231T162140>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31SCB_20231231T162138>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31SBV_20231231T162142>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31SBD_20231231T1621

In [14]:
items = [pystac.Item.from_dict(item) for item in stac_table_to_items(table_head)]
items

[<Item id=S2B_MSIL2A_20231231T114409_R123_T29TMJ_20231231T150806>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCK_20231231T162343>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCJ_20231231T162355>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCH_20231231T162350>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCG_20231231T162354>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCF_20231231T162151>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TCE_20231231T162147>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TBG_20231231T162352>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TBF_20231231T162153>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31TBE_20231231T162152>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31SCD_20231231T162143>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31SCC_20231231T162140>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31SCB_20231231T162138>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31SBV_20231231T162142>,
 <Item id=S2A_MSIL2A_20231231T105441_R051_T31SBD_20231231T1621

In [19]:
# items = [pystac.Item.from_dict(item) for item in stac_table_to_items(table_head)]
print(len(all_items))
map = folium.Map()
layer_control = folium.LayerControl(position="topright", collapsed=True)
fullscreen = folium_plugins.Fullscreen()
style = {"fillColor": "#00000000", "color": "#0000ff", "weight": 1}

footprints = folium.GeoJson(
    gpd.GeoDataFrame.from_features(all_items).to_json(),
    name="Stac Item footprints",
    style_function=lambda x: style,
    control=True,
)

footprints.add_to(map)
layer_control.add_to(map)
fullscreen.add_to(map)
map.fit_bounds(map.get_bounds())
map

1000


### Geofilter

#### A) Original approach

In [14]:
from pygeofilter.backends.sql import to_sql_where
from pygeofilter.parsers.cql2_json import parse as json_parse
from pygeofilter.util import IdempotentDict
from collections import OrderedDict

cql2_filter = {
    "op": "and",
    "args": [
        {
            "op": "between",
            "args": [
                {"property": "datetime"},
                ["2023-12-28T00:00:00Z", "2023-12-28T23:59:59Z"],
            ],
        },
        {"op": "between", "args": [{"property": "eo:cloud_cover"}, [90, 100]]},
        {
            "op": "s_intersects",
            "args": [
                {"property": "geometry"},
                {
                    "type": "Polygon",
                    "coordinates": [
                        [
                            [-9.51346013858793, 38.95450355515311],
                            [-9.51346013858793, 38.22500810801125],
                            [-8.359265560322228, 38.22500810801125],
                            [-8.359265560322228, 38.95450355515311],
                            [-9.51346013858793, 38.95450355515311],
                        ]
                    ],
                },
            ],
        },
    ],
}

# Convert to SQL WHERE clause
sql_where = to_sql_where(json_parse(cql2_filter), IdempotentDict())
print(sql_where)

((("datetime" BETWEEN '2023-12-28T00:00:00Z' AND '2023-12-28T23:59:59Z') AND ("eo:cloud_cover" BETWEEN 90 AND 100)) AND ST_Intersects("geometry",ST_GeomFromWKB(x'01030000000100000005000000D0114E3FE40623C030A6282C2D7A4340D0114E3FE40623C0209FD010CD1C43408053D0A7F1B720C0209FD010CD1C43408053D0A7F1B720C030A6282C2D7A4340D0114E3FE40623C030A6282C2D7A4340')))


In [20]:
sql_query = f"SELECT * EXCLUDE(geometry), ST_AsWKB(geometry) as geometry FROM '{s2_parquet_path}' WHERE {sql_where}"
db_filtered = duckdb.query(sql_query)

NameError: name 'sql_where' is not defined

#### B) Other test

In [14]:
from shapely.geometry import Polygon
from shapely.wkt import dumps

# Define your polygon
polygon = Polygon([
    (-9.51346013858793, 38.95450355515311),
    (-9.51346013858793, 38.22500810801125),
    (-8.359265560322228, 38.22500810801125),
    (-8.359265560322228, 38.95450355515311),
    (-9.51346013858793, 38.95450355515311),
])

# Convert to WKT format
polygon_wkt = dumps(polygon)
print(polygon_wkt)

POLYGON ((-9.5134601385879307 38.9545035551531100, -9.5134601385879307 38.2250081080112523, -8.3592655603222283 38.2250081080112523, -8.3592655603222283 38.9545035551531100, -9.5134601385879307 38.9545035551531100))


In [18]:
cql2_filter2 = {
    "op": "and",
    "args": [
        {
            "op": "between",
            "args": [
                {"property": "datetime"},
                ["2023-12-28T00:00:00Z", "2023-12-28T23:59:59Z"],
            ],
        },
        {"op": "between", "args": [{"property": "eo:cloud_cover"}, [90, 100]]},
        {
            "op": "s_intersects",
            "args": [
                {"property": "geometry"},
                {
                    "type": "WKT",
                    "value": polygon_wkt,  # Use the generated WKT string
                },
            ],
        },
    ],
}
cql2_filter2

{'op': 'and',
 'args': [{'op': 'between',
   'args': [{'property': 'datetime'},
    ['2023-12-28T00:00:00Z', '2023-12-28T23:59:59Z']]},
  {'op': 'between', 'args': [{'property': 'eo:cloud_cover'}, [90, 100]]},
  {'op': 's_intersects',
   'args': [{'property': 'geometry'},
    {'type': 'WKT',
     'value': 'POLYGON ((-9.5134601385879307 38.9545035551531100, -9.5134601385879307 38.2250081080112523, -8.3592655603222283 38.2250081080112523, -8.3592655603222283 38.9545035551531100, -9.5134601385879307 38.9545035551531100))'}]}]}

In [19]:
sql_where2 = to_sql_where(json_parse(cql2_filter2), IdempotentDict())
print(sql_where2)

ValueError: Unable to parse expression node {'type': 'WKT', 'value': 'POLYGON ((-9.5134601385879307 38.9545035551531100, -9.5134601385879307 38.2250081080112523, -8.3592655603222283 38.2250081080112523, -8.3592655603222283 38.9545035551531100, -9.5134601385879307 38.9545035551531100))'}

In [19]:
# # Convert to SQL WHERE clause
# sql_where = to_sql_where(json_parse(cql2_filter), OrderedDict())
# print(sql_where)

In [20]:
sql_query = f"""
    SELECT * EXCLUDE(geometry), CAST(ST_AsWKB(geometry) AS BLOB) AS geometry
    FROM '{s2_parquet_path}'
    WHERE {sql_where2}
"""
db_filtered = duckdb.query(sql_query)


NameError: name 'sql_where2' is not defined

In [21]:
sql_query

"SELECT * EXCLUDE(geometry), ST_AsWKB(geometry) as geometry FROM 's2-stac-api.parquet'"

#### Using `db_filtered`

In [21]:
type(db_filtered)

NameError: name 'db_filtered' is not defined

In [22]:
subset_table = db_filtered.fetch_arrow_table()
# subset_table[0]

NameError: name 'db_filtered' is not defined

In [23]:
items = [pystac.Item.from_dict(item) for item in stac_table_to_items(subset_table)]

items[0]

NameError: name 'subset_table' is not defined

In [26]:
len(items)

1000

In [19]:
map = folium.Map()
layer_control = folium.LayerControl(position="topright", collapsed=True)
fullscreen = folium_plugins.Fullscreen()
style = {"fillColor": "#00000000", "color": "#0000ff", "weight": 1}

footprints = folium.GeoJson(
    gpd.GeoDataFrame.from_features(items).to_json(),
    name="Stac Item footprints",
    style_function=lambda x: style,
    control=True,
)

footprints.add_to(map)
layer_control.add_to(map)
fullscreen.add_to(map)
map.fit_bounds(map.get_bounds())
map